In [1]:
!pip3 install bs4
!pip3 install selenium
!pip3 install webdriver_manager
!pip3 install lxml

You should consider upgrading via the '/Library/Frameworks/Python.framework/Versions/3.9/bin/python3.9 -m pip install --upgrade pip' command.
You should consider upgrading via the '/Library/Frameworks/Python.framework/Versions/3.9/bin/python3.9 -m pip install --upgrade pip' command.
You should consider upgrading via the '/Library/Frameworks/Python.framework/Versions/3.9/bin/python3.9 -m pip install --upgrade pip' command.
You should consider upgrading via the '/Library/Frameworks/Python.framework/Versions/3.9/bin/python3.9 -m pip install --upgrade pip' command.


In [1]:
from bs4 import BeautifulSoup
from selenium import webdriver
import csv

import urllib


import requests

from selenium.webdriver.chrome.options import Options
from selenium.webdriver.chrome.service import Service
from webdriver_manager.chrome import ChromeDriverManager

import requests
import json

In [2]:

class AmazonCrawler:

    def __init__(self):
        self.__base_url = "https://www.amazon.sg"  # Amazon SG
        # init chrome driver
        options = Options()
        options.add_argument('--headless')
        options.add_argument('--disable-gpu')
        service = Service(executable_path=ChromeDriverManager().install())
        self.driver = webdriver.Chrome(options=options, service=service)
        
        
        
    
    def get_product_list(self, search_term: str, limit: int = 100, amazon_category_id: str = None):
        """
        Get product urls and store in list
        """
        search_term_encoded = urllib.parse.quote_plus(search_term)

        url_list = []
        length = 0
        page = 1

        while True:

            if amazon_category_id:
                url = self.__base_url + f"/s?k={search_term_encoded}&page={page}&rh=n%3A{amazon_category_id}&dc"
            else:
                url = self.__base_url + f"/s?k={search_term_encoded}&page={page}"
            bs = self.__get_html_content(url=url)
            s = bs.find_all(attrs={"data-component-type": "s-search-result"})
            print(f"Processing url list, page: {page}")
            print(url)
            for i in s:
                if length >= limit:
                    break
                link_element = i.select(".a-link-normal.s-underline-text.s-underline-link-text.s-link-style.a-text-normal")
                if link_element:
                    url_list.append(link_element[0]["href"])
                    length += 1

            if length < limit:
                page += 1
            else:
                break

        return url_list


        
        
    def get_rating(self,soup):

        try:
            rating = soup.find("i", attrs={'class':'a-icon a-icon-star a-star-4-5'}).string.strip()
        except AttributeError:

            try:
                rating = soup.find("span", attrs={'class':'a-icon-alt'}).string.strip()
                rating = rating.split(" ")[0]
                if rating == 'Previous':
                    rating = ''
            except:
                rating = ""	
        print(rating)
        return rating
    
    def get_price(self,soup):

        try:
            price = soup.find("span", attrs={'class':'a-offscreen'}).string.strip()

        except AttributeError:
            price = ""

        return price
    
    def get_manufacturer(self,soup):
        try:
            manufacturer_tag = soup.find("div", attrs={"id": "prodDetails"}).find("th", text=" Manufacturer ").find_next_sibling("td")
            manufacturer = manufacturer_tag.text.strip()
            manufacturer = manufacturer[1:]
            manufacturer = manufacturer.replace('â€Ž','')
            return manufacturer
        except:
            return ''
    
    
    def get_country_of_origin(self,soup):
        try:
            origin_tag = soup.find("div", attrs={"id": "prodDetails"}).find("th", text=" Country of Origin ").find_next_sibling("td")
            origin = origin_tag.text.strip()
            return origin
        except:
            return ''

    def get_title(self,soup):

        try:
            # Outer Tag Object
            title = soup.find("span", attrs={"id":'productTitle'})

            # Inner NavigableString Object
            title_value = title.string

            # Title as a string value
            title_string = title_value.strip()


        except AttributeError:
            title_string = ""	

        return title_string
    


    def get_image_url(self,soup):
        try:
            image_tag = soup.find("img", id="landingImage")
            image_url = image_tag["src"]
            return image_url
        except:
            return ''



    def get_product_description(self,soup):
    
        list_desc= []
        try:
            info = soup.find("div", {"id": "feature-bullets"})
            for detail in info.find_all('li'):
                if len(list_desc)<5:
                    list_desc.append(detail.text)

            while len(list_desc)<5:
                list_desc.append('')
        except:
            print('no descriptors found')
            list_desc = ['' for _ in range(5)]
            
        return list_desc
            
    def get_product_details(self, product_url: str):
        HEADERS = ({
    'User-Agent': 'Mozilla/5.0 (Macintosh; Intel Mac OS X 10_15_7) AppleWebKit/537.36 (KHTML, like Gecko) Chrome/108.0.0.0 Safari/537.36',
    'Accept-Language': 'en-US, en;q=0.5'})
 
        response = requests.get(product_url,headers=HEADERS)
        #print(product_url)
        print(response.status_code)
        title,price,rating,manufacturer,country_of_origin,image_url = '','','','','',''
        prod_desc = ['' for _ in range(5)]
        if response.status_code == 200:
            
            soup = BeautifulSoup(response.content, "lxml")
            rating  = self.get_rating(soup)
            title = self.get_title(soup)
            price = self.get_price(soup)
            manufacturer = self.get_manufacturer(soup)
            country_of_origin= self.get_country_of_origin(soup)
            image_url = self.get_image_url(soup)
            prod_desc = self.get_product_description(soup)
    
            
            print('price',price)
            print('rating',rating)
            print('title',title)
            print('country_of_origin',country_of_origin)
            print('manufacturer',manufacturer)
            print('image url',image_url)
            
            print('product description',prod_desc)

        return title,price,rating,manufacturer,country_of_origin,image_url,prod_desc

       
    
    
    def get_reviews_details(self, review_url, page_num):
        HEADERS = ({
        'User-Agent': 'Mozilla/5.0 (Macintosh; Intel Mac OS X 10_15_7) AppleWebKit/537.36 (KHTML, like Gecko) Chrome/108.0.0.0 Safari/537.36',
        'Accept-Language': 'en-US, en;q=0.5'})
        print('URL For reviews:', review_url)
        # Make a GET request to the product review page
        for page in range(1, page_num+1):
            review_url = review_url + f'pageNumber={page}/ref=cm_cr_arp_d_paging_btm_next_{page}?pageNumber={page}'
            response = requests.get(review_url, headers=HEADERS)
            reviews = []
            if response.status_code == 200:
                # Parse the HTML content of the response using BeautifulSoup
                soup = BeautifulSoup(response.content, 'html.parser')
                # Find all the review containers on the page
                review_containers = soup.find_all('div', {'data-hook': 'review'})
                for container in review_containers:
                    review = {}
                    # Extract the rating of the review
                    rating_element = container.find('i', {'data-hook': 'cmps-review-star-rating'})
                    if rating_element != None:
                        rating = float(rating_element.span.text.split()[0])
                        review['rating'] = rating
                    else:
                        review['rating'] = 0.0

                    # Extract the title of the review
                    title_element = container.find('span', {'data-hook': 'review-title'})
                    if title_element != None:
                        title = title_element.text.strip()
                        review['title'] = title
                    else:
                        review['title'] = ''

                    # Extract the content of the review
                    content_element = container.find('span', {'data-hook': 'review-body'})

                    if content_element != None:
                        content = content_element.text.strip()
                        review['content'] = content
                    else:
                        review['content'] = ''
                    
                    date_element = container.find('span', {'data-hook': 'review-date'})
                    if date_element != None:
                        date = date_element.text.strip()
                        review['date_country'] = date
                        date = date.split()
                        if 'the' in date:
                            start = date.index('the')
                            end = date.index('on')
                            review['country'] = ' '.join(date[start+1: end-1])
                            review['date'] = date[end+1:]
                        else:
                            start = date.index('in')
                            end = date.index('on')
                            review['country'] = date[start+1]
                            review['date'] = date[end+1:]
                    else:
                        review['date'] = ''
                        review['country'] = ''
                        
                    total_review = soup.find('span', {'class': 'a-size-base'}).text
            
                    if total_review != None:
                        review['total_review'] = total_review.split(' ')[0]
                    else:
                        review['total_review'] = ''

                    reviews.append(review)
                    # Print the extracted information
                    # print(f'Rating: {review.rating}')
                    # print(f'Title: {review.title}')
                    # print(f'Content: {review.content}')
                    #print('Review: ', review)
        
        return reviews
    
    def get_product_ASIN(self, url: str):
        try:
            url_parts = url.split("/")
        # Get the index of "dp" in the URL parts
            dp_index = url_parts.index("dp")
        # Get the ASIN from the URL part after "dp"
            asin = url_parts[dp_index+1]
        #print("Product Code", asin)
            return asin
        except:
            print('cant find asin')
            return ''

    def crawl_content_into_csv(self, search_term: str, limit: int, amazon_category_id=None):
        product_list = self.get_product_list(
            search_term=search_term,
            limit=limit,
            amazon_category_id=amazon_category_id
        )
        with open(f'products_description_{search_term}.csv', 'a+', newline='', encoding="utf-8") as f,open(f'products_reviews_{search_term}.csv', 'a+', newline='', encoding="utf-8") as g:
            writer1 = csv.writer(f)
            writer2 = csv.writer(g)
            writer1.writerow(['product_id','product_link','title','price','rating','manufacturer','country_of_origin','image_url','prod_desc1','prod_desc2','prod_desc3','prod_desc4','prod_desc5'])
            writer2.writerow(['product_id','review_url', 'review_title','review_rating','review_content', 'review_date','total_review' , 'country', 'date_country'])
            for product_slug in product_list:
                row = []
                asin = self.get_product_ASIN(product_slug)
                if asin != '':
                    product_detail_section_url = f'https://www.amazon.sg/dp/{asin}'
                    title,price,rating,manufacturer,country_of_origin,image_url,prod_desc = self.get_product_details(product_detail_section_url)
                    row = [asin,product_detail_section_url, title,price,rating,manufacturer,country_of_origin,image_url,prod_desc[0],prod_desc[1],prod_desc[2],prod_desc[3],prod_desc[4]]
                    row = [str(i or '') for i in row]
                    writer1.writerow(row)
                    print("writing new row...")

                    review_url = f'https://www.amazon.sg/product-reviews/{asin}/'
                    reviews = self.get_reviews_details(review_url,4)
                    
                    print("All Reviews: ", reviews)
                    for review in reviews:
                        row = [asin,review_url,review['title'], review['rating'], review['content'], review['date'],review['total_review'], review['country'], review['date_country']]
                        row = [str(i or '') for i in row]
                        writer2.writerow(row)
                        print("writing new row...")
          

    def __get_html_content(self, url: str) -> BeautifulSoup:
        self.driver.get(url)
        html = self.driver.page_source
        bs = BeautifulSoup(html, 'html.parser')
        return bs

In [3]:
ac = AmazonCrawler()
categories = {
    # "Women’s Fashion": "6833514051",
    "Kitchen & Dining": "6537675051",
    # #"Sports Apparel & Equipment": "6314940051",
    # "DIY & Tools": "6314687051",
    # "Office Products": "6314868051"
}

for search_term, category_id in categories.items():
    ac.crawl_content_into_csv(search_term=search_term, limit=2000, amazon_category_id=category_id)

[WDM] - Downloading: 100%|██████████| 8.82M/8.82M [00:00<00:00, 10.4MB/s]


Processing url list, page: 1
https://www.amazon.sg/s?k=Kitchen+%26+Dining&page=1&rh=n%3A6537675051&dc
Processing url list, page: 2
https://www.amazon.sg/s?k=Kitchen+%26+Dining&page=2&rh=n%3A6537675051&dc
Processing url list, page: 3
https://www.amazon.sg/s?k=Kitchen+%26+Dining&page=3&rh=n%3A6537675051&dc
Processing url list, page: 4
https://www.amazon.sg/s?k=Kitchen+%26+Dining&page=4&rh=n%3A6537675051&dc
Processing url list, page: 5
https://www.amazon.sg/s?k=Kitchen+%26+Dining&page=5&rh=n%3A6537675051&dc
Processing url list, page: 6
https://www.amazon.sg/s?k=Kitchen+%26+Dining&page=6&rh=n%3A6537675051&dc
Processing url list, page: 7
https://www.amazon.sg/s?k=Kitchen+%26+Dining&page=7&rh=n%3A6537675051&dc
Processing url list, page: 8
https://www.amazon.sg/s?k=Kitchen+%26+Dining&page=8&rh=n%3A6537675051&dc
Processing url list, page: 9
https://www.amazon.sg/s?k=Kitchen+%26+Dining&page=9&rh=n%3A6537675051&dc
Processing url list, page: 10
https://www.amazon.sg/s?k=Kitchen+%26+Dining&page=10

/var/folders/27/2h_4klcx3l7dh72hpffzn_040000gn/T/ipykernel_31775/2502369436.py:81: DeprecationWarning: The 'text' argument to find()-type methods is deprecated. Use 'string' instead.
  manufacturer_tag = soup.find("div", attrs={"id": "prodDetails"}).find("th", text=" Manufacturer ").find_next_sibling("td")
/var/folders/27/2h_4klcx3l7dh72hpffzn_040000gn/T/ipykernel_31775/2502369436.py:92: DeprecationWarning: The 'text' argument to find()-type methods is deprecated. Use 'string' instead.
  origin_tag = soup.find("div", attrs={"id": "prodDetails"}).find("th", text=" Country of Origin ").find_next_sibling("td")


All Reviews:  [{'rating': 5.0, 'title': 'LOVE IT', 'content': 'loved it, will purchase another in larger siz', 'date_country': 'Reviewed in the United States 🇺🇸 on 26 January 2023', 'country': 'United States', 'date': ['26', 'January', '2023'], 'total_review': '2,283'}, {'rating': 5.0, 'title': 'PRISTINE WHITE, THICK, HEAVY FABRIC, LOOKS LIKE RESTAURANT, LOOKS PERFECT.', 'content': "I was looking for a tablecloth that will not be pure cotton or linen because it is for everyday use and I wanted very easy maintenance something that will LOOK like cotton without being actual cotton.  It is perfect.The color - pristine white, looks perfect and make it for clean crisp look of the table and makes everything that is on it looking perfect.Looks - elegant, sophisticated. The hem that I was fearing people were concerned about is perfect. I love the way it is finished to perfection. It also promises never run or get undone.Feel - it feels like very heavy sail cloth cotton/linen almost but not as 

In [195]:
url = 'https://www.amazon.sg/dp/B09L4RRS9T'
    
response = requests.get(url)
html_content = response.content


   


In [7]:
from lxml import html 
import requests
import json
from bs4 import BeautifulSoup
asin_1 = 'B0718Y23CQ' #PUT ID HERE, all other code remains the same
asin_2 = 'B0979SR38R' #PUT ID HERE, all other code remains the same
review_url = f'https://www.amazon.sg/product-reviews/{asin_2}'
response = requests.get(review_url)
print("res",response.status_code)
reviews = []
if response.status_code == 200:
                # Parse the HTML content of the response using BeautifulSoup
    soup = BeautifulSoup(response.content, 'html.parser')
                # Find all the review containers on the page
    review_containers = soup.find_all('div', {'data-hook': 'review'})
    for container in review_containers:
                    review = {}
                    # Extract the rating of the review
                    rating_element = container.find('i', {'data-hook': 'cmps-review-star-rating'})
                    if rating_element != None:
                        rating = float(rating_element.span.text.split()[0])
                        print('rating', rating)
                        review['rating'] = rating
                    else:
                        review['rating'] = 0.0

                    # Extract the title of the review
                    title_element = container.find('span', {'data-hook': 'review-title'})
                    if title_element != None:
                        title = title_element.text.strip()
                        review['title'] = title
                    else:
                        review['title'] = ''

                    # Extract the content of the review
                    content_element = container.find('span', {'data-hook': 'review-body'})

                    if content_element != None:
                        content = content_element.text.strip()
                        review['content'] = content
                    else:
                        review['content'] = ''
                    
                    date_element = container.find('span', {'data-hook': 'review-date'})
                    if date_element != None:
                        date = date_element.text.strip()
                        date = date.split()
                        if 'the' in date:
                            start = date.index('the')
                            end = date.index('on')
                            review['country'] = ' '.join(date[start+1: end-1])
                            review['date'] = date[end+1]
                        else:
                            start = date.index('in')
                            review['country'] = date[start+1]
                            review['date'] = date[end+1]
                    else:
                        review['date'] = ''
                        review['country'] = ''
                        
                

                    reviews.append(review)
                    # Print the extracted information
                    # print(f'Rating: {review.rating}')
                    # print(f'Title: {review.title}')
                    # print(f'Content: {review.content}')
                    print('Review: ', review)
        

res 200
rating 5.0
Review:  {'rating': 5.0, 'title': 'Beautiful!!!', 'content': "The stationary papers, they are beautiful. It's vintage looking. I printed a prayer with this paper and my co-worker framed it as a gift for Christmas. It looks more beautiful in the frame. I am glad that I bought this stationary paper. It's thicker than the regular white paper.", 'country': 'United States', 'date': '3'}
rating 4.0
Review:  {'rating': 4.0, 'title': 'Smells funny at first but goes away.', 'content': "I got this paper to wrap soap in. Unfortunately it smells horrible at first, strong chemical smell. I set it aside to use for something else. After a couple of weeks, I noticed the smell had gone away for the most part.  It's nice enough paper, but what the heck are they using on it for it to smell like that?", 'country': 'United States', 'date': '11'}
rating 4.0
Review:  {'rating': 4.0, 'title': 'Good quality paper!', 'content': 'Very good paper, the shipping packaging was a little poor so got